In [1]:
from shapely.geometry import Polygon, MultiPolygon
import geopandas as gpd
import rasterio
from rasterio.windows import from_bounds as wfb
from rasterio.transform import Affine
from rasterio.io import MemoryFile
import os
from rasterio.features import rasterize
from rasterio.transform import from_bounds as tfb
import numpy as np


In [2]:
def drop_z(geom):
    if geom.has_z:
        # Extract only XY coords, drop Z
        if geom.geom_type == 'Polygon':
            exterior = [(x, y) for x, y, z in geom.exterior.coords]
            interiors = [[(x, y) for x, y, z in ring.coords] for ring in geom.interiors]
            return Polygon(exterior, interiors)
        elif geom.geom_type == 'MultiPolygon':
            polygons = []
            for poly in geom.geoms:
                exterior = [(x, y) for x, y, z in poly.exterior.coords]
                interiors = [[(x, y) for x, y, z in ring.coords] for ring in poly.interiors]
                polygons.append(Polygon(exterior, interiors))
            return MultiPolygon(polygons)
    else:
        return geom
    
def add_overlapping_id_with_buffer(gdf1, gdf2, id_col='id', new_col='srtm_id', crs_proj='EPSG:3857', buffer_m=500):
    # Reproject both GeoDataFrames to projected CRS for accurate distance calculations
    gdf1_proj = gdf1.to_crs(crs_proj).copy()
    gdf2_proj = gdf2.to_crs(crs_proj).copy()

    gdf1_proj[new_col] = None
    sindex = gdf2_proj.sindex

    for idx1, geom1 in gdf1_proj.geometry.items():
        possible_matches_index = list(sindex.intersection(geom1.bounds))
        possible_matches = gdf2_proj.iloc[possible_matches_index]

        precise_matches = possible_matches[possible_matches.intersects(geom1)]
        if precise_matches.empty:
            continue

        centroid1 = geom1.centroid
        # Create buffer of specified meters around centroid1
        centroid_buffer = centroid1.buffer(buffer_m)

        # Select geometries whose centroid intersects with the buffer zone
        candidate_matches = precise_matches[precise_matches.geometry.centroid.intersects(centroid_buffer)]

        if not candidate_matches.empty:
            # Assign the id of the first matched geometry (you can modify to handle multiple)
            gdf1_proj.at[idx1, new_col] = candidate_matches.iloc[0][id_col]

    # Optionally transform back to original CRS
    gdf1_final = gdf1_proj.to_crs(gdf1.crs)

    cols = list(gdf1_final.columns)             
    cols.insert(1, cols.pop(cols.index('id')))    
    gdf1_final  = gdf1_final[cols] 
    gdf1_final 

    return gdf1_final

def get_country_tiles(geojson_path, srtm_zip_path, countries_path, country_name):
    # Load data
    gmw_tiles = gpd.read_file(geojson_path)
    srtm_grid = gpd.read_file(f"zip://{srtm_zip_path}")

    # Correct tile data and add srtm id
    gmw_tiles['geometry'] = gmw_tiles['geometry'].apply(drop_z)
    gmw_tiles = add_overlapping_id_with_buffer(gmw_tiles, srtm_grid, id_col='id', new_col='id', crs_proj='EPSG:3857')

    # Filter to overlapping with country
    countries = gpd.read_file(countries_path)
    country = countries[countries['name'] == country_name]

    if gmw_tiles.crs != country.crs:
        country = country.to_crs(gmw_tiles.crs)

    ind_sindex = country.sindex
    overlapping_idx = []

    for idx, geom in gmw_tiles.geometry.items():
        possible_matches_idx = list(ind_sindex.intersection(geom.bounds))
        possible_matches = country.iloc[possible_matches_idx]
        if not possible_matches[possible_matches.intersects(geom)].empty:
            overlapping_idx.append(idx)

    gmw_tiles_country = gmw_tiles.loc[overlapping_idx].copy()

    print("Get country tiles")
    print(f"Projection gmw_tiles: {gmw_tiles.crs}")
    print(f"Projection srtm_grid: {srtm_grid.crs}")
    print(f"Projection countries: {countries.crs}")
    print(f"Projection gmw_tiles_country: {gmw_tiles_country.crs}")
    
    print(f"Found {len(gmw_tiles_country)} polygons overlapping {country_name}.")
    print("\n")
    return gmw_tiles_country

def process_clark_dataset(gmw_tiles_country, year, input_tiff_path, output_tiff_folder):
    # Ensure output directory exists
    os.makedirs(output_tiff_folder, exist_ok=True)

    # Reproject to raster CRS
    with rasterio.open(input_tiff_path) as src:
        raster_crs = src.crs

    gmw_tiles_country_reprojected = gmw_tiles_country.to_crs(raster_crs)

    print("Process Clark dataset")
    print("Projection input_tiff_path:", raster_crs)
    print("Projection gmw_tiles_country_reprojected:", gmw_tiles_country_reprojected.crs)

    # Clip raster with projwin (bounding box)
    for i, row in gmw_tiles_country_reprojected.iloc[:].iterrows():
        bounds = row.geometry.bounds  # (minx, miny, maxx, maxy)
        projwin = [bounds[0], bounds[1], bounds[2], bounds[3]]  # [left, bottom, right, top]
        print(f"Polygon {i} {row["tile"]} {row["id"]} projwin:", projwin)

        with rasterio.open(input_tiff_path) as src:
            window = wfb(*projwin, transform=src.transform)
            clipped_data = src.read(window=window)
            transform = src.window_transform(window)

            profile = src.profile
            profile.update({
                "height": clipped_data.shape[1],
                "width": clipped_data.shape[2],
                "transform": transform
            })

            output_clipped_tif = os.path.join(output_tiff_folder , "CLA_" + row["tile"]+"_"+row["id"]+"_"+ year + ".tif")

            with rasterio.open(output_clipped_tif, "w", **profile) as dst:
                dst.write(clipped_data)

        print(f"Clipped raster saved to: {output_clipped_tif}")
        
    print("\n")

def process_gmw_dataset_vector(input_gmw_path, output_gmw_folder, gmw_tiles_country, year):

    # Ensure output directory exists
    os.makedirs(output_gmw_folder, exist_ok=True)

    # Load GMW vector data
    gmw_gdf = gpd.read_file(f"zip://{input_gmw_path}")

    # Reproject GMW to match tiles (assuming gmw_tiles_country is already loaded)
    if gmw_gdf.crs != gmw_tiles_country.crs:
        gmw_tiles_country = gmw_tiles_country.to_crs(gmw_gdf.crs)

    print("Process GMW dataset")
    print("Projection gmw_gdf:", gmw_gdf.crs)
    print("Projection gmw_tiles_country (reprojected):", gmw_tiles_country.crs)

    # Clip by each tile and save as GeoJSON
    for i, row in gmw_tiles_country.iloc[:].iterrows():

        tile_geom = row.geometry

        # Clip GMW data by this tile
        clipped = gpd.clip(gmw_gdf, tile_geom)

        if not clipped.empty:
            output_path = os.path.join(output_gmw_folder, f"GMW_{row['tile']}_{row['id']}_{year}.geojson")
            clipped.to_file(output_path, driver="GeoJSON")
            print(f"Saved: {output_path}")
        else:
            print(f"Tile {row['tile']} produced an empty clip. Skipped.") 
    
    print("\n")

def process_gmw_dataset_buffer(input_gmw_path, output_gmw_folder, gmw_tiles_country, year, buffers, resolution):

    # Ensure output directory exists
    os.makedirs(output_gmw_folder, exist_ok=True)

    # Load GMW vector data
    gmw_gdf = gpd.read_file(f"zip://{input_gmw_path}")

    # Reproject GMW to match tiles (assuming gmw_tiles_country is already loaded)
    if gmw_gdf.crs != gmw_tiles_country.crs:
        gmw_tiles_country = gmw_tiles_country.to_crs(gmw_gdf.crs)

    print("Process GMW dataset")
    print("Projection gmw_gdf:", gmw_gdf.crs)
    print("Projection gmw_tiles_country (reprojected):", gmw_tiles_country.crs)

    # Clip by each tile and rasterize
    for i, row in gmw_tiles_country.iloc[:].iterrows():
        tile = row['tile']
        tile_id = row['id']
        tile_geom = row.geometry

        # Clip GMW data by this tile
        clipped = gpd.clip(gmw_gdf, tile_geom)

        if not clipped.empty:
            # Dissolve and buffer
            dissolved = clipped.dissolve()
            dissolved = dissolved.to_crs("EPSG:3857")

            for b in buffers: 
                buffered = dissolved.buffer(b)
                buffered_gdf = gpd.GeoDataFrame(geometry=buffered, crs="EPSG:3857").to_crs("EPSG:4326")

                # Get bounds and create transform
                tile_geom_proj = gpd.GeoSeries([tile_geom], crs=gmw_tiles_country.crs).to_crs("EPSG:4326").geometry[0]
                minx, miny, maxx, maxy = tile_geom_proj.bounds
                res = resolution  # meters
                width = int((maxx - minx) / res)
                height = int((maxy - miny) / res)
                transform = tfb(minx, miny, maxx, maxy, width, height)

                # Rasterize
                shapes = ((geom, 1) for geom in buffered_gdf.geometry)
                raster = rasterize(
                    shapes=shapes,
                    out_shape=(height, width),
                    transform=transform,
                    fill=0,
                    dtype='uint8'
                )

                # Save raster
                out_raster_path = os.path.join(output_gmw_folder, f"GMW_{tile}_{tile_id}_{year}_{str(b)}.tif")
                with rasterio.open(
                    out_raster_path, "w",
                    driver="GTiff",
                    height=height,
                    width=width,
                    count=1,
                    dtype='uint8',
                    crs="EPSG:4326",
                    transform=transform
                ) as dst:
                    dst.write(raster, 1)

                print(f"Raster saved: {out_raster_path}")
        else:
            print(f"Tile {tile} produced an empty clip. Skipped.")

def get_buffers(input_path, output_folder, gmw_tiles_country, year, buffers, resolution, dataID):

    # Ensure output directory exists
    os.makedirs(output_folder, exist_ok=True)

    # Load GMW vector data
    gdf = gpd.read_file(input_path)

    # Reproject GMW to match tiles (assuming gmw_tiles_country is already loaded)
    if gdf.crs != gmw_tiles_country.crs:
        gmw_tiles_country = gmw_tiles_country.to_crs(gdf.crs)

    print("Process dataset")
    print(F"Projection {dataID}:", gdf.crs)
    print("Projection gmw_tiles_country (reprojected):", gmw_tiles_country.crs)

    # Clip by each tile and rasterize
    for i, row in gmw_tiles_country.iloc[:].iterrows():
        tile = row['tile']
        tile_id = row['id']
        tile_geom = row.geometry

        # Clip GMW data by this tile
        clipped = gpd.clip(gdf, tile_geom)

        if not clipped.empty:
            # Dissolve and buffer
            dissolved = clipped.dissolve()
            dissolved = dissolved.to_crs("EPSG:3857")

            for b in buffers: 
                buffered = dissolved.buffer(b)
                buffered_gdf = gpd.GeoDataFrame(geometry=buffered, crs="EPSG:3857").to_crs("EPSG:4326")

                # Get bounds and create transform
                tile_geom_proj = gpd.GeoSeries([tile_geom], crs=gmw_tiles_country.crs).to_crs("EPSG:4326").geometry[0]
                minx, miny, maxx, maxy = tile_geom_proj.bounds
                res = resolution  # meters
                width = int((maxx - minx) / res)
                height = int((maxy - miny) / res)
                transform = tfb(minx, miny, maxx, maxy, width, height)

                # Rasterize
                shapes = ((geom, 1) for geom in buffered_gdf.geometry)
                raster = rasterize(
                    shapes=shapes,
                    out_shape=(height, width),
                    transform=transform,
                    fill=0,
                    dtype='uint8'
                )

                # Save raster
                out_raster_path = os.path.join(output_folder, f"{dataID}_{tile}_{tile_id}_{year}_{str(b)}.tif")
                with rasterio.open(
                    out_raster_path, "w",
                    driver="GTiff",
                    height=height,
                    width=width,
                    count=1,
                    dtype='uint8',
                    crs="EPSG:4326",
                    transform=transform
                ) as dst:
                    dst.write(raster, 1)

                print(f"Raster saved: {out_raster_path}")
        else:
            print(f"Tile {tile} produced an empty clip. Skipped.")


def get_thiessen_polygons(input_path, output_folder, gmw_tiles_country, year, resolution, buffer_aoi, dataID):

    # Ensure output directory exists
    os.makedirs(output_folder, exist_ok=True)

    # Load GMW vector data
    gdf = gpd.read_file(input_path)
    original_crs = gdf.crs
    gdf = gpd.read_file(input_path).to_crs("EPSG:3857")

    # Reproject GMW to match tiles (assuming gmw_tiles_country is already loaded)
    if gdf.crs != gmw_tiles_country.crs:
        gmw_tiles_country = gmw_tiles_country.to_crs(gdf.crs)

    print("Process dataset")
    print(F"Projection {dataID}:", gdf.crs)
    print("Projection gmw_tiles_country (reprojected):", gmw_tiles_country.crs)

    # Clip by each tile and rasterize
    for i, row in gmw_tiles_country.iloc[:].iterrows():
        tile_geom = row.geometry.buffer(buffer_aoi)

        # Clip GMW data by this tile
        clipped = gpd.clip(gdf, tile_geom)
        clipped = clipped.to_crs(original_crs)

        if not clipped.empty:
            output_path = os.path.join(output_folder, f"GTS_{row['tile']}_{row['id']}_{year}.geojson")
            clipped.to_file(output_path, driver="GeoJSON")
            print(f"Saved: {output_path}")
        else:
            print(f"Tile {row['tile']} produced an empty clip. Skipped.")
 
    print("\n")

def get_tiles_vector(output_folder, gmw_tiles_country, year):
    os.makedirs(output_folder, exist_ok=True)

    for i, row in gmw_tiles_country.iterrows():
        # Convert the row to a GeoDataFrame using .loc[[i]]
        tile_geom = gmw_tiles_country.loc[[i]]

        output_path = os.path.join(output_folder, f"TIL_{row['tile']}_{row['id']}_{year}.geojson")
        tile_geom.to_file(output_path, driver="GeoJSON")

        print(f"Saved: {output_path}")

    print("\n")


def get_tiles_vector_with_buffer(output_folder, gmw_tiles_country, year, buffer_crs, buffer_meters):
    os.makedirs(output_folder, exist_ok=True)

    original_crs = gmw_tiles_country.crs

    for i, row in gmw_tiles_country.iterrows():
        # Select row as GeoDataFrame
        tile_geom = gmw_tiles_country.loc[[i]]

        # Reproject to buffer CRS
        tile_geom_proj = tile_geom.to_crs(buffer_crs)

        # Apply 50 km buffer
        tile_geom_proj['geometry'] = tile_geom_proj.buffer(buffer_meters)

        # Reproject back to original CRS
        tile_geom_buffered = tile_geom_proj.to_crs(original_crs)

        # Output path
        output_path = os.path.join(output_folder, f"TIL_{row['tile']}_{row['id']}_{year}_{str(buffer_meters)}.geojson")

        # Save to GeoJSON
        tile_geom_buffered.to_file(output_path, driver="GeoJSON")

        print(f"Saved: {output_path}")

    print("\n")


### Parameters and paths


In [3]:
# Parameters
country_name = 'Indonesia'
tile_year = '2025'

year_clark = '2022'
year_gmw = '2020'
buffers_gmw = [0, 500, 2500, 10000]
resolution_gmw = 0.0002222222222219999985 # Around 24.74 meters 0.0002222222222219999985
year_sho = '2025'
buffers_sho = [250, 500]
resolution_sho = 0.0002222222222219999985 # Around 24.74 meters
year_gts = '2025'
resolution_gts = 0.0002222222222219999985 # Around 24.74 meters
buffer_aoi_gts = 100000

# General paths
geojson_path = r"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\1_Tiles\gmw_v3_tiles.geojson"
srtm_zip_path = r"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\1_Tiles\srtm_grid_1deg.zip"
output_tile_path = fr"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\1_Tiles\{country_name}"
countries_path = r"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\2_Countries\countries.geojson"
input_tiff_path = fr"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\3_Clark_classification\{country_name}_Landcover_Change_Maps_1999_2014_2018_2020_2022\{country_name}_Landcover_{year_clark}_v2exp.tif"
output_tiff_folder = fr"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\3_Clark_classification\{country_name}"
input_gmw_path = fr"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\4_GMW\6894273\gmw_v3_{year_gmw}_vec.zip"
output_gmw_folder = fr"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\4_GMW\{country_name}"
input_sho_path = r"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\5_Shoreline\GSHHS_i_L1_5km_dissolved_gtsm_coastline_exploded.gpkg"
output_sho_folder = fr"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\5_Shoreline\{country_name}"
input_gts_path = r"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\8_Tides\gtsm_tidal_indicators_2022.gpkg"
output_gts_folder = fr"C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\8_Tides\{country_name}"

### Process tiles

In [4]:
gmw_tiles_country = get_country_tiles(geojson_path, srtm_zip_path, countries_path, country_name)
gmw_tiles_country = gmw_tiles_country[gmw_tiles_country['tile']=='N00E117']
# gmw_tiles_country = gmw_tiles_country.iloc[:10,:]
get_tiles_vector(output_tile_path, gmw_tiles_country, tile_year)
get_tiles_vector_with_buffer(output_tile_path, gmw_tiles_country, tile_year, "EPSG:3857", 10000)

Get country tiles
Projection gmw_tiles: EPSG:4326
Projection srtm_grid: EPSG:4326
Projection countries: EPSG:4326
Projection gmw_tiles_country: EPSG:4326
Found 276 polygons overlapping Indonesia.


Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\1_Tiles\Indonesia\TIL_N00E117_S01E117_2025.geojson


Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\1_Tiles\Indonesia\TIL_N00E117_S01E117_2025_10000.geojson




### Clark dataset processing

In [5]:
# process_clark_dataset(gmw_tiles_country, year_clark, input_tiff_path, output_tiff_folder)
# This function is replaced by 3_process_clark.py code

### GMW dataset processing

In [ ]:
process_gmw_dataset_vector(input_gmw_path, output_gmw_folder, gmw_tiles_country, year_gmw)
process_gmw_dataset_buffer(input_gmw_path, output_gmw_folder, gmw_tiles_country, year_gmw, buffers_gmw, resolution_gmw)

Process GMW dataset
Projection gmw_gdf: EPSG:4326
Projection gmw_tiles_country (reprojected): EPSG:4326
Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\4_GMW\Indonesia\GMW_N00E117_S01E117_2020.geojson


Process GMW dataset
Projection gmw_gdf: EPSG:4326
Projection gmw_tiles_country (reprojected): EPSG:4326
Raster saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\4_GMW\Indonesia\GMW_N00E117_S01E117_2020_0.tif
Raster saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\4_GMW\Indonesia\GMW_N00E117_S01E117_2020_500.tif


### Shoreline dataset processing

In [23]:
# get_buffers(input_sho_path, output_sho_folder, gmw_tiles_country, year_sho, buffers_sho, resolution_sho, 'SHO')

### GTSM dataset processing

In [25]:
get_thiessen_polygons(input_gts_path, output_gts_folder, gmw_tiles_country, year_gts, resolution_gts, buffer_aoi_gts, 'GTS')

Process dataset
Projection GTS: EPSG:3857
Projection gmw_tiles_country (reprojected): EPSG:3857
Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\8_Tides\Indonesia\GTS_S08E140_S09E140_2025.geojson
Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\8_Tides\Indonesia\GTS_S01E109_S02E109_2025.geojson
Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\8_Tides\Indonesia\GTS_N03E096_N02E096_2025.geojson
Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\8_Tides\Indonesia\GTS_S02E108_S03E108_2025.geojson
Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\8_Tides\Indonesia\GTS_S03E126_S04E126_2025.geojson
Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\8_Tides\Indonesia\GTS_S03E133_S04E133_2025.geojson
Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\8_Tides\Indonesia\GTS_S08E124_S09E124_2025.geojson
Saved: C:\Ocean\Work\Projects\2025\Mangroves\Data\0_Workflow\8_Tides\Indonesia\GTS_N02E120_N01E120_2025.geojson
Saved: C

In [ ]:
# Base map: all tiles
m = gmw_tiles.explore(
    color="blue",
    style_kwds=dict(weight=1),
    name="All Tiles"
)

# Add overlapping tiles (highlighted in red)
gmw_tiles_overlapping_indonesia.explore(
    m=m,
    color="yellow",
    style_kwds=dict(weight=2),
    name="Overlapping with Indonesia"
)

# Add Indonesia boundary (highlighted in blue)
indonesia.explore(
    m=m,
    color="blue",
    style_kwds=dict(weight=2, fill=False),
    name="Indonesia"
)

# Show map
m

In [10]:
import geopandas as gpd
import pandas as pd
from shapely.geometry import Point, LineString

# --- LOAD DATA ---
file_path = r'p:\11211992-tki-mangrove-restoration\01_data\GIN_annual_coastlinesnewdatabase.xlsx'
df = pd.read_excel(file_path)

# Create GeoDataFrame
gdf = gpd.GeoDataFrame(
    df,
    geometry=gpd.points_from_xy(df['Intersect_lon'], df['Intersect_lat']),
    crs='EPSG:4326'  # WGS84
)

# Project to UTM zone for distance in meters (you may want to adjust zone depending on location)
gdf = gdf.to_crs(epsg=32630)  # Example: UTM Zone 30N. Change to fit your region.
gdf

transect_id country_id continent country_name  changerate  flag_sandy  \
0     BOX_120_138_1        GIN    Africa       Guinea   -0.721394           0   
1     BOX_120_138_2        GIN    Africa       Guinea   23.900228           0   
2     BOX_120_138_3        GIN    Africa       Guinea    0.325190           0   
3     BOX_120_138_4        GIN    Africa       Guinea   12.720222           0   
4     BOX_120_138_5        GIN    Africa       Guinea   -0.280219           0   
...             ...        ...       ...          ...         ...         ...   
1396  BOX_120_092_2        GIN    Africa       Guinea   -0.085719           0   
1397  BOX_120_092_3        GIN    Africa       Guinea   -0.304848           0   
1398  BOX_120_092_4        GIN    Africa       Guinea    0.013182           0   
1399  BOX_120_092_5        GIN    Africa       Guinea    0.045844           0   
1400  BOX_120_092_6        GIN    Africa       Guinea    0.521075           0   

      no_shorelines                                                 dt  \
0                27  [0.0, 2.00141002211, 3.00074607966, 4.00008213...   
1                28  [0.0, 2.00141002211, 3.00074607966, 4.00008213...   
2                25  [0.0, 2.00141002211, 4.00008213721, 5.00215610...   
3                26  [0.0, 2.00141002211, 4.00008213721, 5.00215610...   
4                26  [0.0, 2.00141002211, 4.00008213721, 5.00215610...   
...             ...                                                ...   
1396             26  [2.00141002211, 4.00008213721, 5.00215610177, ...   
1397             26  [2.00141002211, 4.00008213721, 5.00215610177, ...   
1398             26  [2.00141002211, 4.00008213721, 5.00215610177, ...   
1399             27  [0.0, 2.00141002211, 4.00008213721, 5.00215610...   
1400             26  [2.00141002211, 4.00008213721, 5.00215610177, ...   

                                                   dist        RMSE  \
0     [667.2971744321869, 688.2593170940436, 590.212...   10.198030   
1     [563.8547748270179, 1372.0799026502502, 520.07...  346.112856   
2     [814.4243780662981, 1409.181999377978, 816.417...    6.790827   
3     [1919.3530227647232, 1917.4780679970195, 974.8...  240.892656   
4     [558.7977684773145, 559.1314364108003, 583.593...    6.920151   
...                                                 ...         ...   
1396  [10.386510255878939, 18.036874705639196, 21.04...   11.974588   
1397  [396.08682254128803, 413.5287941046127, 499.20...   13.806049   
1398  [221.51308658793687, 241.05817835151424, 302.8...    9.196955   
1399  [1673.4146451301103, 785.1318077013193, 788.23...   12.687321   
1400  [962.573344095634, 941.8154524776764, 925.8208...   13.993398   

                     outliers_1 outliers_2  Timespan    intercept  \
0                           [6]        [2]        32   661.552186   
1     [0, 1, 4, 5, 6, 7, 8, 23]         []        29   464.804229   
2              [1, 2, 3, 4, 20]        [0]        21  1394.646535   
3                   [6, 11, 15]       [22]        31  1600.197428   
4                            []        [5]        32   571.525605   
...                         ...        ...       ...          ...   
1396                        [6]        [9]        30    26.677486   
1397                         []        [2]        30   417.821343   
1398                         []     [2, 6]        30   235.027406   
1399                         []        [0]        30   790.055615   
1400                         []        [4]        30   947.701233   

      Intersect_lon  Intersect_lat                         geometry  
0        -13.188671       9.179224  POINT (-624998.729 1030750.683)  
1        -13.184772       9.177207   POINT (-624570.35 1030511.807)  
2        -13.180851       9.175191  POINT (-624139.451 1030272.925)  
3        -13.176380       9.174989   POINT (-623641.43 1030236.033)  
4        -13.171954       9.175436  POINT (-623146.369 1030272.027)  
...             ...            ...          

In [ ]:
# --- EXTRACT ID COMPONENTS ---
gdf['base_id'] = gdf['transect_id'].apply(lambda x: '_'.join(x.split('_')[:3]))
gdf['point_num'] = gdf['transect_id'].apply(lambda x: int(x.split('_')[-1]))

# Sort points
gdf_sorted = gdf.sort_values(by=['base_id', 'point_num'])

# --- GENERATE LINES WITH DISTANCE FILTER ---
lines = []

for base_id, group in gdf_sorted.groupby('base_id'):
    group = group.sort_values('point_num').reset_index(drop=True)
    current_line = [group.geometry.iloc[0]]

    for i in range(1, len(group)):
        prev_num = group['point_num'].iloc[i - 1]
        curr_num = group['point_num'].iloc[i]
        dist = group.geometry.iloc[i].distance(group.geometry.iloc[i - 1])

        # Only connect if consecutive AND within 600 meters
        if curr_num == prev_num + 1 and dist <= 600:
            current_line.append(group.geometry.iloc[i])
        else:
            if len(current_line) >= 2:
                lines.append({'transect_id': base_id, 'geometry': LineString(current_line)})
            current_line = [group.geometry.iloc[i]]

    if len(current_line) >= 2:
        lines.append({'transect_id': base_id, 'geometry': LineString(current_line)})

# Create GeoDataFrame with lines
lines_gdf = gpd.GeoDataFrame(lines, crs=gdf.crs)

# --- EXPLORE BOTH ---
# Reproject to EPSG:4326 for display
gdf = gdf.to_crs(epsg=4326)
lines_gdf = lines_gdf.to_crs(epsg=4326)

m = gdf.explore(color="blue", marker_kwds={"radius": 4}, tooltip="transect_id")
lines_gdf.explore(m=m, color="red", tooltip="transect_id")


In [12]:
import geopandas as gpd
import pandas as pd
from shapely.geometry import Point, LineString
import folium

# --- LOAD DATA ---
file_path = r'p:\11211992-tki-mangrove-restoration\01_data\GIN_annual_coastlinesnewdatabase.xlsx'
df = pd.read_excel(file_path)

# Create GeoDataFrame with WGS84 coordinates
gdf = gpd.GeoDataFrame(
    df,
    geometry=gpd.points_from_xy(df['Intersect_lon'], df['Intersect_lat']),
    crs='EPSG:4326'
)

# Project to UTM (metric system, adjust EPSG if necessary)
gdf = gdf.to_crs(epsg=32630)  # Use appropriate UTM zone

# --- EXTRACT ID COMPONENTS ---
gdf['base_id'] = gdf['transect_id'].apply(lambda x: '_'.join(x.split('_')[:3]))
gdf['point_num'] = gdf['transect_id'].apply(lambda x: int(x.split('_')[-1]))

# Sort points
gdf_sorted = gdf.sort_values(by=['base_id', 'point_num'])

# --- GENERATE LINES WITH DISTANCE FILTER ---
lines = []

for base_id, group in gdf_sorted.groupby('base_id'):
    group = group.sort_values('point_num').reset_index(drop=True)
    current_line = [group.geometry.iloc[0]]

    for i in range(1, len(group)):
        prev_num = group['point_num'].iloc[i - 1]
        curr_num = group['point_num'].iloc[i]
        dist = group.geometry.iloc[i].distance(group.geometry.iloc[i - 1])

        # Only connect if consecutive AND within 600 meters
        if curr_num == prev_num + 1 and dist <= 600:
            current_line.append(group.geometry.iloc[i])
        else:
            if len(current_line) >= 2:
                lines.append({'transect_id': base_id, 'geometry': LineString(current_line)})
            current_line = [group.geometry.iloc[i]]

    if len(current_line) >= 2:
        lines.append({'transect_id': base_id, 'geometry': LineString(current_line)})

# Create GeoDataFrame with lines
lines_gdf = gpd.GeoDataFrame(lines, crs=gdf.crs)

# --- CREATE BUFFERS ---
buffer_250 = lines_gdf.copy()
buffer_250['geometry'] = buffer_250.geometry.buffer(250)

buffer_500 = lines_gdf.copy()
buffer_500['geometry'] = buffer_500.geometry.buffer(500)

# --- REPROJECT TO WGS84 FOR DISPLAY ---
gdf = gdf.to_crs(epsg=4326)
lines_gdf = lines_gdf.to_crs(epsg=4326)
buffer_250 = buffer_250.to_crs(epsg=4326)
buffer_500 = buffer_500.to_crs(epsg=4326)

# --- EXPLORE ALL LAYERS ---
m = gdf.explore(color="blue", marker_kwds={"radius": 4}, tooltip="transect_id", name="Points")
m = lines_gdf.explore(m=m, color="red", tooltip="transect_id", name="Lines")
m = buffer_250.explore(m=m, color="green", style_kwds={'fillOpacity': 0.2}, name="Buffer 250m")
m = buffer_500.explore(m=m, color="orange", style_kwds={'fillOpacity': 0.1}, name="Buffer 500m")

# Add layer control
# folium.LayerControl().add_to(m)
m


In [2]:
import geopandas as gpd
import pandas as pd
from shapely.geometry import Point, LineString
from shapely.ops import voronoi_diagram
import folium

# --- STEP 1: LOAD POINT DATA ---
file_path = r'p:\11211992-tki-mangrove-restoration\01_data\GIN_annual_coastlinesnewdatabase.xlsx'
df = pd.read_excel(file_path)

# Create GeoDataFrame in WGS84
gdf = gpd.GeoDataFrame(
    df,
    geometry=gpd.points_from_xy(df['Intersect_lon'], df['Intersect_lat']),
    crs='EPSG:4326'
)

# Project to metric CRS (UTM zone 30N – change if needed)
gdf = gdf.to_crs(epsg=32630)

# --- STEP 2: EXTRACT ID COMPONENTS AND SORT ---
gdf['base_id'] = gdf['transect_id'].apply(lambda x: '_'.join(x.split('_')[:3]))
gdf['point_num'] = gdf['transect_id'].apply(lambda x: int(x.split('_')[-1]))
gdf_sorted = gdf.sort_values(by=['base_id', 'point_num'])

# --- STEP 3: CONNECT POINTS INTO LINES ---
lines = []
for base_id, group in gdf_sorted.groupby('base_id'):
    group = group.sort_values('point_num').reset_index(drop=True)
    current_line = [group.geometry.iloc[0]]

    for i in range(1, len(group)):
        prev_num = group['point_num'].iloc[i - 1]
        curr_num = group['point_num'].iloc[i]
        dist = group.geometry.iloc[i].distance(group.geometry.iloc[i - 1])

        if curr_num == prev_num + 1 and dist <= 600:
            current_line.append(group.geometry.iloc[i])
        else:
            if len(current_line) >= 2:
                lines.append({'transect_id': base_id, 'geometry': LineString(current_line)})
            current_line = [group.geometry.iloc[i]]

    if len(current_line) >= 2:
        lines.append({'transect_id': base_id, 'geometry': LineString(current_line)})

lines_gdf = gpd.GeoDataFrame(lines, crs=gdf.crs)

# --- STEP 4: CREATE BUFFERS ---
buffer_250 = lines_gdf.copy()
buffer_250['geometry'] = buffer_250.geometry.buffer(250)

buffer_500 = lines_gdf.copy()
buffer_500['geometry'] = buffer_500.geometry.buffer(500)

# --- STEP 5: GENERATE THIESSEN (VORONOI) POLYGONS ---
multi_point = gdf.unary_union
bounds = multi_point.convex_hull.buffer(1000)
vor = voronoi_diagram(multi_point, envelope=bounds)

voronoi_gdf = gpd.GeoDataFrame(
    geometry=[poly for poly in vor.geoms],
    crs=gdf.crs
)

# Assign transect_id to Voronoi polygons via spatial join
# point_poly_join = gpd.sjoin(
#     voronoi_gdf, gdf[['transect_id', 'geometry']],
#     how='left',
#     predicate='contains'
# ).drop(columns='index_right').dropna(subset=['transect_id'])

# # --- STEP 6: CLIP THIESSEN POLYGONS TO 500 m BUFFER ---
# clipped_voronoi = gpd.overlay(point_poly_join, buffer_500, how='intersection')

# # --- STEP 7: REPROJECT ALL LAYERS TO EPSG:4326 FOR DISPLAY ---
# gdf = gdf.to_crs(epsg=4326)
# lines_gdf = lines_gdf.to_crs(epsg=4326)
# buffer_250 = buffer_250.to_crs(epsg=4326)
# buffer_500 = buffer_500.to_crs(epsg=4326)
# clipped_voronoi = clipped_voronoi.to_crs(epsg=4326)

# # --- STEP 8: DISPLAY INTERACTIVE MAP ---
# m = gdf.explore(color="blue", marker_kwds={"radius": 4}, tooltip="transect_id", name="Points")
# m = lines_gdf.explore(m=m, color="red", tooltip="transect_id", name="Lines")
# m = buffer_250.explore(m=m, color="green", style_kwds={'fillOpacity': 0.2}, name="Buffer 250 m")
# m = buffer_500.explore(m=m, color="orange", style_kwds={'fillOpacity': 0.1}, name="Buffer 500 m")
# m = clipped_voronoi.explore(m=m, column="transect_id", cmap="Pastel1", tooltip="transect_id", name="Thiessen (Clipped)")

# # folium.LayerControl().add_to(m)
# m


C:\Users\fuentesm\AppData\Local\Temp\ipykernel_20828\1776269334.py:57: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  multi_point = gdf.unary_union


In [24]:
import geopandas as gpd
import pandas as pd
from shapely.geometry import Point, LineString
from shapely.ops import voronoi_diagram
import folium

# --- STEP 1: LOAD POINT DATA ---
file_path = r'p:\11211992-tki-mangrove-restoration\01_data\GIN_annual_coastlinesnewdatabase.xlsx'
df = pd.read_excel(file_path)

# Create GeoDataFrame in WGS84
gdf = gpd.GeoDataFrame(
    df,
    geometry=gpd.points_from_xy(df['Intersect_lon'], df['Intersect_lat']),
    crs='EPSG:4326'
)

# Project to metric CRS (UTM zone 30N – change if needed)
gdf = gdf.to_crs(epsg=32630)

# --- STEP 2: EXTRACT ID COMPONENTS AND SORT ---
gdf['base_id'] = gdf['transect_id'].apply(lambda x: '_'.join(x.split('_')[:3]))
gdf['point_num'] = gdf['transect_id'].apply(lambda x: int(x.split('_')[-1]))
gdf_sorted = gdf.sort_values(by=['base_id', 'point_num'])

# --- STEP 3: CONNECT POINTS INTO LINES ---
lines = []
for base_id, group in gdf_sorted.groupby('base_id'):
    group = group.sort_values('point_num').reset_index(drop=True)
    current_line = [group.geometry.iloc[0]]

    for i in range(1, len(group)):
        prev_num = group['point_num'].iloc[i - 1]
        curr_num = group['point_num'].iloc[i]
        dist = group.geometry.iloc[i].distance(group.geometry.iloc[i - 1])

        if curr_num == prev_num + 1 and dist <= 600:
            current_line.append(group.geometry.iloc[i])
        else:
            if len(current_line) >= 2:
                lines.append({'transect_id': base_id, 'geometry': LineString(current_line)})
            current_line = [group.geometry.iloc[i]]

    if len(current_line) >= 2:
        lines.append({'transect_id': base_id, 'geometry': LineString(current_line)})

lines_gdf = gpd.GeoDataFrame(lines, crs=gdf.crs)

# --- STEP 4: CREATE BUFFERS ---
buffer_250 = lines_gdf.copy()
buffer_250['geometry'] = buffer_250.geometry.buffer(250)

buffer_500 = lines_gdf.copy()
buffer_500['geometry'] = buffer_500.geometry.buffer(500)

# --- STEP 5: GENERATE THIESSEN (VORONOI) POLYGONS ---
multi_point = gdf.unary_union
bounds = multi_point.convex_hull.buffer(1000)
vor = voronoi_diagram(multi_point, envelope=bounds)

voronoi_gdf = gpd.GeoDataFrame(
    geometry=[poly for poly in vor.geoms],
    crs=gdf.crs
)

# --- STEP 6: CLIP VORONOI POLYGONS WITH 500m BUFFER ---
buffer_500_union = buffer_500.unary_union  # Dissolve all buffers into one geometry

voronoi_clipped = voronoi_gdf.copy()
voronoi_clipped['geometry'] = voronoi_clipped.geometry.intersection(buffer_500_union)

# Remove empty geometries that fall outside the buffer
voronoi_clipped = voronoi_clipped[~voronoi_clipped.is_empty].reset_index(drop=True)
voronoi_clipped.explore()

# Optional: save or inspect the clipped Voronoi polygons
# voronoi_clipped.to_file('voronoi_clipped.shp')  # Example to save shapefile



C:\Users\fuentesm\AppData\Local\Temp\ipykernel_18640\737664007.py:57: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  multi_point = gdf.unary_union
C:\Users\fuentesm\AppData\Local\Temp\ipykernel_18640\737664007.py:67: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  buffer_500_union = buffer_500.unary_union  # Dissolve all buffers into one geometry
